In [ ]:
import sys

import numpy as np
import pandas as pd

In [11]:
train_data = pd.read_parquet(
    "../data/processed/chrome/08_12_2022/train_set_01.parquet.gzip"
)

test_data = pd.read_parquet(
    "../data/processed/chrome/08_12_2022/test_set_01.parquet.gzip"
)

In [9]:
train_data

pragma                    content-type  \
256683      None  text/javascript; charset=utf-8   
14233       None          application/javascript   
100818  no-cache                       image/gif   
106109  no-cache                            None   
126395      None        text/html; charset=utf-8   
...          ...                             ...   
31179       None                       image/png   
9931    no-cache                            None   
256544      None             binary/octet-stream   
184101      None                 application/xml   
157680      None  text/javascript; charset=utf-8   

                        last-modified accept-ranges  \
256683                           None          None   
14233   mon, 08 aug 2022 21:56:59 gmt          None   
100818                           None          None   
106109                           None          None   
126395                           None          None   
...                               ...           ...   
31179   fri, 12 nov 2021 05:09:38 gmt         bytes   
9931    fri, 12 aug 2022 09:22:13 gmt          None   
256544  mon, 20 dec 2021 02:24:19 gmt         bytes   
184101  thu, 26 apr 2018 18:25:27 gmt         bytes   
157680  wed, 03 aug 2022 12:04:53 gmt          None   

                                      etag  \
256683                15601544113783900868   
14233                                 None   
100818                                None   
106109                                None   
126395                                None   
...                                    ...   
31179                      "618df712-2509"   
9931                                  None   
256544  "4abfa4888190370d347034f9fa43c804"   
184101                 w/"29a-1630333f5d8"   
157680                   0x8da754860160d55   

                                                      p3p x-xss-protection  \
256683  policyref="https://www.googleadservices.com/pa...                0   
14233                                                None             None   
100818  policyref="https://www.googleadservices.com/pa...                0   
106109                                               None             None   
126395                                               None             None   
...                                                   ...              ...   
31179                                                None             None   
9931                                                 None             None   
256544                                               None             None   
184101                                               None    1; mode=block   
157680                                               None             None   

       x-content-type-options            strict-transport-security  \
256683                nosniff                                 None   
14233                 nosniff  max-age=31536000; includesubdomains   
100818                nosniff                                 None   
106109                   None                                 None   
126395                   None  max-age=15724800; includesubdomains   
...                       ...                                  ...   
31179                    None                          max-age=300   
9931                  nosniff                                 None   
256544                   None                                 None   
184101                nosniff            max-age=31536000; preload   
157680                   None                                 None   

       x-robots-tag  ... xc-version x-amzn-waf-action generated  \
256683         None  ...       None              None      None   
14233          None  ...       None              None      None   
100818         None  ...       None              None      None   
106109         None  ...       None              None      None   
126395         None  ...       None              None     

In [13]:
train_data = train_data.iloc[:, 6:]
test_data = test_data.iloc[:, 6:]

In [14]:
for elem in train_data.iloc[:, :-1].columns.values.tolist():
    train_data[f"{elem}_binary"] = np.where(train_data[elem].isnull(), 0, 1)
    test_data[f"{elem}_binary"] = np.where(test_data[elem].isnull(), 0, 1)

<ipython-input-14-8c2879514956>:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  train_data[f"{elem}_binary"] = np.where(train_data[elem].isnull(), 0, 1)
<ipython-input-14-8c2879514956>:3: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_data[f"{elem}_binary"] = np.where(test_data[elem].isnull(), 0, 1)
<ipython-input-14-8c2879514956>:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.

In [19]:
train_data = train_data.iloc[:, 5309:]
test_data = test_data.iloc[:, 5309:]

In [22]:
for elem in train_data.columns.values.tolist():
    train_data[elem] = train_data[elem].astype("uint8")
    test_data[elem] = test_data[elem].astype("uint8")

In [24]:
def label_as_last_column(dataset):
    temp_cols = dataset.columns.tolist()
    index_col = dataset.columns.get_loc("tracker")
    new_col_order = (
            temp_cols[0:index_col]
            + temp_cols[index_col + 1:]
            + temp_cols[index_col: index_col + 1]
    )
    return new_col_order


reordered_cols = label_as_last_column(train_data)
train_data = train_data[reordered_cols]
test_data = test_data[reordered_cols]

In [26]:
train_data.to_parquet(
    f"../data/processed/chrome/08_12_2022/train_set_all_binary.parquet.gzip",
    compression="gzip",
)

test_data.to_parquet(
    f"../data/processed/chrome/08_12_2022/test_set_all_binary.parquet.gzip",
    compression="gzip",
)